In [60]:
import torch
from torch.utils.data import Dataset
import json
import os
import torch.nn as nn
import torch.nn.functional as func
from torch.utils.data import DataLoader
import torch.optim as optim
from os.path import expanduser
import splitfolders
import shutil
import glob
import numpy as np
from sklearn.model_selection import train_test_split

In [61]:
class KpVelDataset(Dataset):
    def __init__(self, json_folder):
        super(KpVelDataset, self).__init__()
        self.data = []
        for json_file in sorted(os.listdir(json_folder)):
            if json_file.endswith('_combined.json'):
                with open(os.path.join(json_folder, json_file), 'r') as file:
                    data = json.load(file)
                    start_kp = data['start_kp']
                    next_kp = data['next_kp']
                    velocity = data['velocity']
                    self.data.append((start_kp, next_kp, velocity))

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        start_kp, next_kp, velocity = self.data[idx]
        start_kp_flat = torch.tensor([kp for sublist in start_kp for kp in sublist[0]])
        next_kp_flat = torch.tensor([kp for sublist in next_kp for kp in sublist[0]])
        velocity = torch.tensor(velocity)
        return start_kp_flat, next_kp_flat, velocity
    

In [62]:
def train_test_split(src_dir):
#     dst_dir_img = src_dir + "images"
    dst_dir_anno = src_dir + "annotations"
    
    if os.path.exists(dst_dir_anno):
        print("folders exist")
    else:
        os.mkdir(dst_dir_anno)
        
#     for jpgfile in glob.iglob(os.path.join(src_dir, "*.jpg")):
#         shutil.copy(jpgfile, dst_dir_img)

    for jsonfile in glob.iglob(os.path.join(src_dir, "*_combined.json")):
        shutil.copy(jsonfile, dst_dir_anno)
        
    output = root_dir + "split_folder_reg"
    
    splitfolders.ratio(src_dir, # The location of dataset
                   output=output, # The output location
                   seed=42, # The number of seed
                   ratio=(0.7, 0.15, 0.15), # The ratio of split dataset
                   group_prefix=None, # If your dataset contains more than one file like ".jpg", ".pdf", etc
                   move=False # If you choose to move, turn this into True
                   )
    
#     shutil.rmtree(dst_dir_img)
    shutil.rmtree(dst_dir_anno)
    
    return output  

In [63]:
# class VelRegModel(nn.Module):
#     def __init__(self, input_size):
#         super(VelRegModel, self).__init__()
#         self.fc1 = nn.Linear(input_size * 2, 1024)  # Assuming start_kp and next_kp are concatenated
#         self.fc2 = nn.Linear(1024, 512)
#         self.fc3 = nn.Linear(512,256)
#         self.fc4 = nn.Linear(256,128)
#         self.fc5 = nn.Linear(128,64)
#         self.fc6 = nn.Linear(64,64)
#         self.fc7 = nn.Linear(64,6)  # Output size is 3 for velocity

#     def forward(self, start_kp, velocity):
#         x = torch.cat((start_kp, velocity), dim=1)
#         x = func.relu(self.fc1(x))
#         x = func.relu(self.fc2(x))
#         x = func.relu(self.fc3(x))
#         x = func.relu(self.fc4(x))
#         x = func.relu(self.fc5(x))
#         x = func.relu(self.fc6(x))
#         x = self.fc7(x)
#         return x

In [72]:
import torch
import torch.nn as nn
import torch.nn.functional as F

class KeypointRegressionNet(nn.Module):
    def __init__(self):
        super(KeypointRegressionNet, self).__init__()
        # Define the architecture
        self.fc1 = nn.Linear(21, 128)  # 18 keypoints + 3 velocity values
        self.fc2 = nn.Linear(128, 256)
        self.fc3 = nn.Linear(256, 128)
        self.fc4 = nn.Linear(128, 18)  # Output size is 18 (6 keypoints * 3 values each)

    def forward(self, start_kp, velocity):
        # Flatten start keypoints and concatenate with velocity
        x = torch.cat((start_kp, velocity), dim=1)
        
        # Forward pass through the network
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = F.relu(self.fc3(x))
        x = self.fc4(x)  # No activation function in the last layer
        return x

In [70]:
# Initialize dataset and data loader
# to generalize home directory. User can change their parent path without entering their home directory
num_epochs = 250
batch_size = 128
v = 3
root_dir = '/home/jc-merlab/Pictures/panda_data/panda_sim_vel/vel_reg_sim_test/'
print(root_dir)
split_folder_path = train_test_split(root_dir)
dataset = KpVelDataset(root_dir)
data_loader = DataLoader(dataset, batch_size=batch_size, shuffle=True)

# Initialize model
model = KeypointRegressionNet()  # Adjust input_size as necessary
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.005)

# Training loop
for epoch in range(num_epochs):
    for start_kp, next_kp, velocity in data_loader:
        optimizer.zero_grad()
        velocity = velocity.squeeze(1)
        print(start_kp.shape)
        print(velocity.shape)
        output = model(start_kp, velocity)
        loss = criterion(output, next_kp)
        loss.backward()
        optimizer.step()
        print("output", output)
    print(f'Epoch {epoch+1}, Loss: {loss.item()}')
    
# Save the trained model
model_save_path = f'/home/jc-merlab/Pictures/Data/trained_models/reg_nkp_b{batch_size}_e{num_epochs}_v{v}.pth'
torch.save(model.state_dict(), model_save_path)
print(f"Model saved to {model_save_path}")


/home/jc-merlab/Pictures/panda_data/panda_sim_vel/vel_reg_sim_test/


Copying files: 3132 files [00:00, 18637.30 files/s]


torch.Size([128, 18])
torch.Size([128, 3])
output tensor([[-17.2105,   8.0819,  -3.7918,  ...,  -0.3458,   9.0517,   9.5128],
        [ -9.7912,   7.3680,  -5.9000,  ...,  -1.2536,   8.7140,   4.1146],
        [-14.5960,   6.1304,  -3.8637,  ...,  -0.3554,   7.0163,   7.2547],
        ...,
        [-13.0491,   5.2479,  -3.7508,  ...,   0.1268,   5.1856,   6.8825],
        [ -9.6725,   7.1833,  -5.8597,  ...,  -0.9611,   8.2416,   3.8241],
        [-14.0880,   5.4400,  -3.6499,  ...,  -0.0720,   6.3218,   7.1921]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 18])
torch.Size([128, 3])
output tensor([[ 80.7178, 172.8227,  65.7700,  ...,  95.0945,  93.8538,  16.8076],
        [ 99.2576, 216.3378,  84.2275,  ..., 117.8697, 118.1428,  22.9346],
        [ 79.3023, 167.1315,  62.3937,  ...,  86.6561,  89.1970,  13.0872],
        ...,
        [ 72.5383, 155.4098,  59.1620,  ...,  84.2514,  83.3890,  13.5605],
        [ 73.9411, 158.8500,  60.8121,  ...,  87.1790,  85.3799,  14.6534],
    

output tensor([[241.8555, 333.4318,   5.4125,  ..., 266.0714, 171.3859,   1.8070],
        [289.1658, 395.1394,   8.6299,  ..., 445.3755, 287.6058,  -4.2604],
        [245.2279, 336.1860,   5.9110,  ..., 305.9469, 175.1573,  -1.2418],
        ...,
        [268.8633, 386.7881,  -7.3931,  ...,  80.6208, 211.1143,   4.0283],
        [250.3639, 340.0231,   6.5317,  ..., 381.9652, 210.6390,  -4.6008],
        [260.9583, 369.6223,   0.7599,  ..., 161.8573, 188.0839,   7.9722]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 18])
torch.Size([128, 3])
output tensor([[252.1105, 353.1423,   5.9937,  ..., 263.0735, 212.4309,   1.8475],
        [242.1610, 337.2092,   4.5602,  ..., 306.2841, 178.6939,  -2.8553],
        [266.9996, 371.8618,   4.8455,  ..., 433.0881, 274.7920,  -7.3946],
        ...,
        [265.1457, 370.6563,   6.5815,  ..., 384.9132, 273.6104,  -3.8414],
        [251.5038, 351.7184,   5.6113,  ..., 241.4981, 189.1081,   2.4739],
        [247.9777, 347.2054,   5.7056,  ..., 31

torch.Size([128, 18])
torch.Size([128, 3])
output tensor([[ 2.6863e+02,  3.8331e+02, -1.9355e+00,  ...,  4.4001e+02,
          2.5193e+02, -1.9937e+00],
        [ 2.4995e+02,  3.5879e+02, -3.1307e+00,  ...,  3.9387e+02,
          2.9976e+02, -5.7590e-01],
        [ 2.5606e+02,  3.6600e+02, -2.9653e+00,  ...,  3.5946e+02,
          3.4669e+02,  1.3017e+00],
        ...,
        [ 2.5374e+02,  3.6175e+02, -6.3663e-01,  ...,  3.1540e+02,
          3.2973e+02,  1.5884e+00],
        [ 2.5520e+02,  3.6304e+02, -2.9487e-01,  ...,  3.8127e+02,
          1.4249e+02, -6.8753e-01],
        [ 2.5059e+02,  3.5887e+02, -2.7168e+00,  ...,  3.6462e+02,
          3.1934e+02,  4.7737e-01]], grad_fn=<AddmmBackward0>)
torch.Size([128, 18])
torch.Size([128, 3])
output tensor([[ 2.5649e+02,  3.6904e+02,  1.0801e+00,  ...,  2.9155e+02,
          1.0218e+02, -2.2506e+00],
        [ 2.6290e+02,  3.7462e+02, -2.2180e+00,  ...,  1.0554e+02,
          2.0012e+02,  1.7199e+00],
        [ 2.6685e+02,  3.8382e+02, -

...

output tensor([[ 2.4963e+02,  3.5661e+02, -9.9041e-01,  ...,  2.7098e+02,
          1.0876e+02,  1.6926e-01],
        [ 2.5214e+02,  3.5918e+02,  5.9971e-03,  ...,  3.4461e+02,
          2.1888e+02,  8.0693e-01],
        [ 2.5165e+02,  3.5931e+02, -3.6377e-01,  ...,  1.0646e+02,
          2.0635e+02,  5.2569e-01],
        ...,
        [ 2.5031e+02,  3.5722e+02, -7.1262e-01,  ...,  2.3313e+02,
          1.1179e+02,  5.2678e-01],
        [ 2.5002e+02,  3.5694e+02, -3.9348e-01,  ...,  2.7299e+02,
          1.0037e+02,  3.8051e-01],
        [ 2.5343e+02,  3.6131e+02, -2.6925e-01,  ...,  5.3602e+01,
          3.0091e+02,  4.0941e-01]], grad_fn=<AddmmBackward0>)
torch.Size([128, 18])
torch.Size([128, 3])
output tensor([[266.4313, 378.5429,   2.3285,  ...,  79.5474, 201.4805,   1.1092],
        [265.4235, 377.4096,   1.5236,  ..., 286.3219, 165.8961,   0.9546],
        [264.4542, 376.0184,   2.5211,  ..., 466.4637, 266.4492,   0.7082],
        ...,
        [265.4211, 376.9419,   1.4581,  ...,

output tensor([[257.5973, 367.0148,   0.6739,  ..., 292.5225, 234.8377,   0.8915],
        [257.0556, 366.7437,   0.8122,  ..., 230.0999, 104.5219,   0.7428],
        [258.5092, 368.1083,   1.0662,  ..., 308.6748, 252.6377,   0.5520],
        ...,
        [257.7826, 367.1085,   0.9164,  ...,  93.8220, 157.7689,   0.5662],
        [256.9153, 366.7531,   0.7873,  ..., 244.4329, 103.0209,   0.7349],
        [257.4084, 366.6411,   0.7999,  ..., 167.1524, 115.2486,   0.8158]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 18])
torch.Size([128, 3])
output tensor([[258.7241, 368.9793,   0.9992,  ..., 291.6711,  99.2633,   0.8553],
        [259.9311, 368.8837,   0.9639,  ...,  78.4158, 288.3798,   0.7242],
        [259.6653, 369.3020,   1.5117,  ..., 382.1628, 344.9129,   0.9130],
        ...,
        [258.6785, 368.7648,   1.4252,  ..., 284.0938,  95.8711,   0.8458],
        [259.3817, 369.4249,   1.2117,  ..., 435.4612, 247.0018,   0.9558],
        [259.8397, 369.4427,   1.2951,  ..., 38

torch.Size([128, 18])
torch.Size([128, 3])
output tensor([[257.1927, 365.4221,   0.6176,  ..., 379.5749, 345.0918,   0.9764],
        [257.3721, 365.6395,   1.0667,  ..., 400.2399, 189.5462,   1.2783],
        [257.0952, 365.6794,   0.9112,  ..., 282.5886, 172.3105,   1.0382],
        ...,
        [257.5035, 365.5558,   1.2646,  ..., 349.0352, 189.0096,   1.1143],
        [257.0039, 365.7343,   1.2593,  ..., 322.0249, 157.5295,   1.1571],
        [256.8873, 365.8492,   0.6649,  ..., 418.4243, 238.5150,   0.7659]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 18])
torch.Size([128, 3])
output tensor([[258.5067, 367.2408,   0.8417,  ..., 411.2480, 350.7558,   1.0670],
        [258.7168, 368.1088,   1.0543,  ..., 300.5524, 241.0503,   0.9644],
        [258.7688, 368.0066,   0.9923,  ..., 388.6164, 128.6055,   1.1641],
        ...,
        [259.2720, 367.9824,   0.8615,  ..., 197.4364, 114.5279,   0.9317],
        [258.5329, 368.0403,   1.4321,  ..., 319.5089, 164.7003,   1.0837],
    

torch.Size([128, 18])
torch.Size([128, 3])
output tensor([[255.8227, 363.5770,   0.8866,  ..., 179.1214, 122.6226,   0.8574],
        [256.2375, 365.1920,   0.8870,  ..., 429.3319, 245.1533,   0.5410],
        [256.2411, 364.1041,   1.1965,  ..., 288.0987,  82.5220,   0.5527],
        ...,
        [255.6701, 364.2141,   0.6960,  ..., 278.0697, 105.0202,   0.6959],
        [255.6635, 363.7432,   0.9005,  ..., 182.5868, 113.0598,   0.7685],
        [255.3340, 363.2931,   1.2051,  ..., 360.2234, 258.9237,   0.5381]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 18])
torch.Size([128, 3])
output tensor([[260.2127, 369.6142,   0.9690,  ..., 353.6959, 322.6679,   1.3338],
        [261.2409, 371.0004,   1.3186,  ..., 453.7888, 241.6299,   1.3326],
        [259.7126, 369.6455,   0.8346,  ..., 223.7558, 108.3927,   1.2184],
        ...,
        [259.8606, 369.7755,   1.0421,  ..., 164.1664, 117.5684,   1.2965],
        [261.0792, 371.1751,   0.8754,  ..., 442.0934, 239.8562,   1.2118],
    

output tensor([[258.8342, 368.0084,   1.2386,  ..., 265.5524, 205.2001,   0.7043],
        [258.4431, 367.8278,   0.9590,  ..., 293.3424, 167.0519,   0.9623],
        [259.4543, 368.9725,   1.5803,  ..., 411.5758, 352.5380,   1.1906],
        ...,
        [258.8702, 368.1381,   0.9444,  ..., 334.2533, 261.1833,   1.0491],
        [258.6695, 367.8842,   1.2478,  ..., 353.6036, 224.3502,   1.4366],
        [258.1398, 367.6743,   1.5604,  ..., 346.0152, 351.2582,   1.0898]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 18])
torch.Size([128, 3])
output tensor([[ 2.5730e+02,  3.6643e+02, -1.6627e-01,  ...,  3.1948e+02,
          2.5787e+02,  6.4230e-01],
        [ 2.5722e+02,  3.6601e+02, -2.7620e-01,  ...,  3.0373e+02,
          2.0448e+02,  8.9320e-01],
        [ 2.5690e+02,  3.6544e+02, -2.4043e-01,  ...,  3.3145e+02,
          3.0509e+02,  9.0115e-01],
        ...,
        [ 2.5711e+02,  3.6636e+02, -1.4310e-01,  ...,  2.8987e+02,
          2.3118e+02,  9.1475e-01],
        [ 2.570

In [76]:
def test_model(model_path, test_data_dir):
    # Load the test dataset
    test_dataset = KpVelDataset(test_data_dir)
    test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)

    # Initialize the model and load the saved state
    model = KeypointRegressionNet()
    model.load_state_dict(torch.load(model_path))
    model.eval()

    # Criterion for evaluation
    criterion = nn.MSELoss()
    total_loss = 0

    # No gradient needed for evaluation
    with torch.no_grad():
        for start_kp, next_kp, velocity in test_loader:
            output = model(start_kp, velocity)
            for i in range(start_kp.size(0)):
                individual_start_kp = start_kp[i]
                individual_next_kp = next_kp[i]
                individual_velocity = velocity[i]
                predicted_next_kp = output[i]

                print("Start KP:", individual_start_kp)
                print("Next KP:", individual_next_kp)
                print("Actual Velocity:", individual_velocity)
                print("Predicted Velocity:", predicted_next_kp)
                print("-----------------------------------------")
            loss = criterion(output, next_kp)
            total_loss += loss.item()
            
    # Calculate the average loss
    avg_loss = total_loss / len(test_loader)
    print(f'Average Test Loss: {avg_loss}')

# Usage
model_path = '/home/jc-merlab/Pictures/Data/trained_models/reg_nkp_b128_e250_v0.pth'  # Update with your model path
test_data_dir = '/home/jc-merlab/Pictures/panda_data/panda_sim_vel/vel_reg_sim_test/split_folder_reg/test/annotations/'  # Update with your test data path
test_model(model_path, test_data_dir)

Start KP: tensor([257.9522, 366.9199,   1.0000, 257.9597, 283.0131,   1.0000, 179.8257,
        298.1946,   1.0000, 175.8687, 277.7923,   1.0000, 240.1268, 202.5661,
          1.0000, 262.0790, 205.0822,   1.0000])
Next KP: tensor([257.9522, 366.9199,   1.0000, 257.9597, 283.0131,   1.0000, 179.8260,
        298.1959,   1.0000, 175.8685, 277.7937,   1.0000, 240.1280, 202.5687,
          1.0000, 262.0802, 205.0853,   1.0000])
Actual Velocity: tensor([0.0000, 0.0000, 0.3000])
Predicted Velocity: tensor([257.7654, 366.7654,   0.9178, 257.9145, 283.0347,   1.1408, 179.7099,
        298.4261,   1.0625, 175.4932, 277.9028,   0.8915, 240.3632, 202.5495,
          1.0117, 261.5081, 204.5572,   1.1235])
-----------------------------------------
Start KP: tensor([257.9522, 366.9199,   1.0000, 257.9597, 283.0131,   1.0000, 179.8213,
        298.1725,   1.0000, 175.8698, 277.7691,   1.0000, 240.1633, 202.5730,
          1.0000, 262.1147, 205.0952,   1.0000])
Next KP: tensor([257.9522, 366.9199,   

Next KP: tensor([257.9522, 366.9199,   1.0000, 257.9597, 283.0131,   1.0000, 303.7598,
        217.8956,   1.0000, 320.7623, 229.8525,   1.0000, 419.9565, 231.2956,
          1.0000, 442.5465, 231.8152,   1.0000])
Actual Velocity: tensor([0.0000, 0.0893, 0.0000])
Predicted Velocity: tensor([258.3449, 367.1544,   0.7209, 258.5476, 283.7431,   1.3077, 303.9985,
        219.0668,   1.1029, 320.3009, 230.5019,   0.9057, 420.4909, 232.1425,
          1.0414, 442.1325, 232.9416,   1.1690])
-----------------------------------------
Start KP: tensor([257.9522, 366.9199,   1.0000, 257.9597, 283.0131,   1.0000, 303.7598,
        217.8956,   1.0000, 320.7623, 229.8525,   1.0000, 419.9565, 231.2956,
          1.0000, 442.5465, 231.8152,   1.0000])
Next KP: tensor([257.9522, 366.9199,   1.0000, 257.9597, 283.0131,   1.0000, 303.7659,
        217.8999,   1.0000, 320.7673, 229.8584,   1.0000, 419.9698, 230.4328,
          1.0000, 442.5634, 230.7548,   1.0000])
Actual Velocity: tensor([0.0000, 0.0893,